In [2]:
import os
from itertools import chain

from tf.app import use
from tf.core.files import dirMake

In [3]:
A = use("ETCBC/bhsa:clone", checkout="clone", hoist=globals())

**Locating corpus resources ...**

## Find multiple word phrases with equal `nu` on first and last word

### In TF, by means of a query:

In [17]:
query = """
phrase
    =: fi:word
    # la:word
    :=

fi .nu. la
"""

resultsQ = A.search(query)

  0.90s 15522 results


In [18]:

A.show(resultsQ, end=3, condenseType="clause")

### In TF, by means of hand-coding:

In [19]:
resultsH = []

for p in F.otype.s("phrase"):
    ws = L.d(p, otype="word")
    if len(ws) < 2:
        continue
    fi = ws[0]
    la = ws[-1]
    if F.nu.v(fi) != F.nu.v(la):
        continue
    resultsH.append((p, fi, la))

len(resultsH)

15522

### Check

In [20]:
set(resultsQ) == set(resultsH)

True

## In STAM

Challenges:

### Find the first and last word in each phrase

Given a phrase, we need to find its words.
Well, a phrase is an annotation with key `otype` and value `phrase` and target some word annotations.
These target annotations are easy to get, by means of the `annotations()` method on annotations.

Then we have to find the first and last words among these targets.

**That is currently difficult!**

You need a concept of order between annotations.
One possibility is to put sequence numbers in the data, as annotations.
But that is very cumbersome, because you need to refer to yet another level of annotation.
And it will inflate the data.

The other possibility is "canonical ordering".
Annotations that target the text can be ordered by their targets.
A target is a subset of textual positions. Two such subsets can be ordered as follows:

* if A is a subset of B then B <= A
* if B is a subset of A then A <= B
* if A and B are no subsets of each other, the set that has the smallest element that does not belong to the other set, is the smallest.

As part of the index building, you could create the rank of each annotation in this ordering.

Annotations that target annotations that are already canonically ordered, can themselves be canonically ordered w.r.t. their targets.

Without this, the user will need to implement sorting in ad-hoc ways.

### Retrieve values for the first and last word

Given the annotations for the first and last word in a phrase, we have to find annotations with key `nu`
and target these words, and read off their value.

**That is currently difficult!**

A way out is this:

As preparation, before looping through the phrases:
Make a dict that associates word annotation identifiers with `nu`-values:

* retrieve all annotations that have key `nu`, for each annotation:
* pick the target, it is a word annotation, pick its id and use that as key in the dict
* pick the data and from that the value and use that as value in the dict

Then, for each phrase with at least two words:

* retrieve the first word and from there the `nu`-value for that word
* retrieve the second word and from there the `nu`-value for that word
* compare the two values. If they are equal, we have a hit.

This can be improved if the API offers an efficient function to look up values.
That could be a pre computation of all those dictionaries.

Even better: those dictionaries could be the primary data!

In [22]:
import stam

from memutil import memUsage
memUsage()

workDir = f"{A.tempDir}/stam"
storeC = stam.AnnotationStore(file=f"{workDir}/bhsa.store.stam.csv")

Current:  3.01 GB
Delta:    3.01 GB


In [44]:
aDataSet = list(storeC.annotationsets())[0]

In [45]:
def stamOtype(otype):
    otypeData = aDataSet.find_data("otype", otype)
    otypeAnnos = otypeData[0].annotations()
    return otypeAnnos

def idsOf(annos):
    return {a.id() for a in annos}

In [59]:
# get the word annotations, sorted, and the phrase annotations

def getPos(wordAnno):
    t = wordAnno.textselections()[0]
    return (t.begin(), t.end())

wordAnnos = stamOtype("word")
wordIds = idsOf(wordAnnos)
phraseAnnos = stamOtype("phrase")

In [60]:
wordAnnos = sorted(wordAnnos, key=getPos)

In [47]:
# make a rank of the word annos

wordRank = {anno.id(): i for (i, anno) in enumerate(wordAnnos)}

In [49]:
# get the phrase annotations together with their first and last word

phrases = []

for pAnno in phraseAnnos:
    words = pAnno.annotations()
    if len(words) < 2:
        continue
    sortedWords = sorted(words, key=lambda x: wordRank[x.id()])
    phrases.append((p, words[0], words[-1]))

len(phrases)

78754

In [50]:
# intermediate check with TF

query = """
phrase
    =: word
    # word
    :=
"""
results = A.search(query)

  0.90s 78754 results


In [51]:
# get the `nu` information ready
# we collect a dict keyed by word id with values the grammatical number of the word

nuKey = aDataSet.key("nu")
nuAnnos = nuKey.annotations()

nuValue = {}

for nuAnno in nuAnnos:
    value = nuAnno.data()[0].value()
    word = list(nuAnno.annotations())[0]

    nuValue[word.id()] = value


In [52]:
# check some values

for wordAnno in wordAnnos[0:11]:
    print(f"{wordAnno} {nuValue[wordAnno.id()]}")

בְּ NA
רֵאשִׁ֖ית  sg
בָּרָ֣א  sg
אֱלֹהִ֑ים  pl
אֵ֥ת  NA
הַ NA
שָּׁמַ֖יִם  pl
וְ NA
אֵ֥ת  NA
הָ NA
אָֽרֶץ00  sg


So far so good!

In [53]:
# now compute the final result

resultsSTAM = [x for x in phrases if nuValue[x[1].id()] == nuValue[x[2].id()]]
len(resultsSTAM)

15522

Perfect!

## Now in one go

In order to see the performance, let's do this again in one go.

In [54]:
# The complete task in one go

def getNicePhrases():
    aDataSet = list(storeC.annotationsets())[0]
    wordAnnos = sorted(stamOtype("word"), key=getPos)
    wordIds = idsOf(wordAnnos)
    wordRank = {anno.id(): i for (i, anno) in enumerate(wordAnnos)}

    phraseAnnos = stamOtype("phrase")
    phrases = []

    for pAnno in phraseAnnos:
        words = pAnno.annotations()
        if len(words) < 2:
            continue
        sortedWords = sorted(words, key=lambda x: wordRank[x.id()])
        phrases.append((p, words[0], words[-1]))

    nuKey = aDataSet.key("nu")
    nuAnnos = nuKey.annotations()

    nuValue = {}

    for nuAnno in nuAnnos:
        value = nuAnno.data()[0].value()
        word = list(nuAnno.annotations())[0]

        nuValue[word.id()] = value

    results = [x for x in phrases if nuValue[x[1].id()] == nuValue[x[2].id()]]
    print(len(results))
    return results

In [55]:
resultsSTAM = getNicePhrases()

15522


The execution times for this task were

TF query | TF hand coding | STAM
--- | --- | ---
0.9 | 0.2 | 2.0

But in STAM we can move quite a bit out of the task:

1. sorting the words should be taken care of during the index building/loading when loading the STAM dataset (saves 0.3 sec)
2. retrieving the `nu` value should be optimized (could save 0.9 sec)